In [1]:
import pandas as pd
import eli5
import numpy as np
from sklearn.preprocessing import StandardScaler
from sklearn.compose import ColumnTransformer
from sklearn.pipeline import Pipeline
from sklearn.model_selection import train_test_split, GridSearchCV
from sklearn.metrics import accuracy_score, classification_report
from sklearn.linear_model import LogisticRegression
from sklearn.decomposition import PCA
from sklearn import svm
from sklearn.tree import DecisionTreeClassifier
from sklearn.ensemble import RandomForestClassifier
from os.path import exists
import train
import joblib
from utils import main
import shap
from xgboost import XGBClassifier
shap.initjs()

### Download and process data

In [2]:
datasets = ["LUAD", "LUSC", "KIRP", "KIRC"]
for data in datasets:
    if not exists(f"data/{data}.pkl"):
        main()

### Load Preprocessed data

In [3]:
LUAD = pd.read_pickle("data/LUAD.pkl")
LUSC = pd.read_pickle("data/LUSC.pkl")

In [4]:
LUAD.shape , LUSC.shape

((586, 60488), (551, 60488))

In [5]:
LUAD = LUAD.head(LUSC.shape[0])

In [6]:
LUAD["Target"] = 1
LUSC["Target"] = 2

In [7]:
df = pd.concat([LUAD,LUSC])

del LUAD, LUSC

In [8]:
def extract_features(df):
    features = list(df.columns[:-1])
    y = df['Target']
    X = df[features]
    return X,y

def split_data(X,y):
    X_train, X_test, y_train, y_test = train_test_split(X, y, test_size = 0.2, random_state = 42, stratify=y)
    return X_train, X_test, y_train, y_test

In [9]:
X, y = extract_features(df)
X_train, X_test, y_train, y_test = split_data(X, y)
feature_names = list(X.columns)

In [10]:
dataname = "LUSCLUAD"
if not exists(f"models/{dataname}_LR.mdl"):
    train.run_logistic_regression(X_train, X_test, y_train, y_test, dataname)
if not exists(f"models/{dataname}_SVM.mdl"):
    train.run_svm(X_train, X_test, y_train, y_test, dataname)
if not exists(f"models/{dataname}_DT.mdl"):
    train.run_decision_trees(X_train, X_test, y_train, y_test, dataname)
if not exists(f"models/{dataname}_RF.mdl"):
    train.run_random_forest(X_train, X_test, y_train, y_test, dataname)
if not exists(f"models/{dataname}_XGB.mdl"):
    train.run_xgboost(X_train, X_test, y_train, y_test, dataname)

### Loading the models

In [11]:
rf_model = joblib.load(f"models/{dataname}_RF.mdl")
lr_model = joblib.load(f"models/{dataname}_LR.mdl")
dt_model = joblib.load(f"models/{dataname}_DT.mdl")
svm_model = joblib.load(f"models/{dataname}_SVM.mdl")
xgb_model = joblib.load(f"models/{dataname}_XGB.mdl")

### Comparing results

In [12]:
i = 14
X_test.iloc[[i]]

Ensembl_ID        ENSG00000000003.13  ENSG00000000005.5  ENSG00000000419.11  \
TCGA-73-4666-01A           12.105581                3.0           11.199672   

Ensembl_ID        ENSG00000000457.12  ENSG00000000460.15  ENSG00000000938.11  \
TCGA-73-4666-01A           10.632086           10.731319           10.932953   

Ensembl_ID        ENSG00000000971.14  ENSG00000001036.12  ENSG00000001084.9  \
TCGA-73-4666-01A           14.111054           12.542306          12.914011   

Ensembl_ID        ENSG00000001167.13  ...  ENSGR0000275287.3  \
TCGA-73-4666-01A           12.721099  ...                0.0   

Ensembl_ID        ENSGR0000276543.3  ENSGR0000277120.3  ENSGR0000280767.1  \
TCGA-73-4666-01A                0.0                0.0                0.0   

Ensembl_ID        ENSGR0000281849.1  __no_feature  __ambiguous  \
TCGA-73-4666-01A                0.0     21.670822    21.940781   

Ensembl_ID        __too_low_aQual  __not_aligned  __alignment_not_unique  
TCGA-73-4666-01A              0.0            0.0               24.984917  

[1 rows x 60488 columns]

In [13]:
y_test.iloc[[i]]

TCGA-73-4666-01A    1
Name: Target, dtype: int64

##### SVM prediction accuracy

In [14]:
y_pred = svm_model.predict(X_test)

print("SVM Accuracy: ", accuracy_score(y_test, y_pred))

print("Classification report:\n",
        classification_report(y_test, y_pred))

eli5.show_weights(svm_model.named_steps["model"], feature_names=feature_names, top=20)

SVM Accuracy:  0.995475113122172
Classification report:
               precision    recall  f1-score   support

           1       0.99      1.00      1.00       111
           2       1.00      0.99      1.00       110

    accuracy                           1.00       221
   macro avg       1.00      1.00      1.00       221
weighted avg       1.00      1.00      1.00       221



##### Logistic Regression Accuracy

In [15]:
y_pred = lr_model.predict(X_test)

print("LR Accuracy: ", accuracy_score(y_test, y_pred))

print("Classification report:\n",
        classification_report(y_test, y_pred))

eli5.show_weights(lr_model.named_steps["model"], feature_names=feature_names, top=20)

LR Accuracy:  1.0
Classification report:
               precision    recall  f1-score   support

           1       1.00      1.00      1.00       111
           2       1.00      1.00      1.00       110

    accuracy                           1.00       221
   macro avg       1.00      1.00      1.00       221
weighted avg       1.00      1.00      1.00       221



##### Random Forest Accuracy

In [16]:
y_pred = rf_model.predict(X_test)

print("RF Accuracy: ", accuracy_score(y_test, y_pred))

print("Classification report:\n",
    classification_report(y_test, y_pred))

eli5.show_weights(rf_model.named_steps["model"], feature_names=feature_names, top=20)

RF Accuracy:  0.9864253393665159
Classification report:
               precision    recall  f1-score   support

           1       0.98      0.99      0.99       111
           2       0.99      0.98      0.99       110

    accuracy                           0.99       221
   macro avg       0.99      0.99      0.99       221
weighted avg       0.99      0.99      0.99       221



##### Decision Trees Accuracy

In [17]:
y_pred = dt_model.predict(X_test)

print("DT Accuracy: ", accuracy_score(y_test, y_pred))

print("Classification report:\n",
    classification_report(y_test, y_pred))

eli5.show_weights(dt_model.named_steps["model"], feature_names=feature_names, top=20)

DT Accuracy:  0.9638009049773756
Classification report:
               precision    recall  f1-score   support

           1       0.93      1.00      0.97       111
           2       1.00      0.93      0.96       110

    accuracy                           0.96       221
   macro avg       0.97      0.96      0.96       221
weighted avg       0.97      0.96      0.96       221



##### XGBoost Accuracy

In [18]:
y_pred = xgb_model.predict(X_test)

print("XGB Accuracy: ", accuracy_score(y_test, y_pred))

print("Classification report:\n",
    classification_report(y_test, y_pred))

XGB Accuracy:  0.9366515837104072
Classification report:
               precision    recall  f1-score   support

           1       0.91      0.96      0.94       111
           2       0.96      0.91      0.93       110

    accuracy                           0.94       221
   macro avg       0.94      0.94      0.94       221
weighted avg       0.94      0.94      0.94       221



##### XGBoost Explain

In [19]:
explainer = shap.TreeExplainer(xgb_model.named_steps["model"])

# observations = X_train.sample(100, random_state=42)
observations = X_test.iloc[[i]]
shap_values = explainer.shap_values(observations)

shap.force_plot(explainer.expected_value, shap_values[0], 
                features=observations.iloc[[0]].values, feature_names=feature_names)

Setting feature_perturbation = "tree_path_dependent" because no background data was given.


#### Decision Tree

In [20]:
eli5.show_prediction(dt_model.named_steps["model"], 
                     X_test.iloc[[i]],
                     feature_names=feature_names, show_feature_values=True, top=20)

In [21]:
explainer = shap.TreeExplainer(dt_model.named_steps["model"])

Setting feature_perturbation = "tree_path_dependent" because no background data was given.


In [22]:
# observations = X_train.sample(100, random_state=42)
observations = X_test.values

In [23]:
shap_values = explainer.shap_values(observations[17])

In [24]:
shap_values[0].shape

(60488,)

In [25]:
shap.force_plot(explainer.expected_value[0], shap_values[0],
                features=observations[i], feature_names=feature_names)

#### Random forest

In [26]:
eli5.show_prediction(rf_model.named_steps["model"],
                     X_test.iloc[[i]],
                     feature_names=feature_names, show_feature_values=True, top=20)

In [27]:
explainer = shap.TreeExplainer(rf_model.named_steps["model"])

# observations = X_train.sample(100, random_state=42)
observations = X_test.iloc[[i]]
shap_values = explainer.shap_values(observations, check_additivity=False)

shap.force_plot(explainer.expected_value[0], shap_values[0], 
                features=observations.iloc[[0]].values, feature_names=feature_names)

Setting feature_perturbation = "tree_path_dependent" because no background data was given.


#### Logistic Regression

In [28]:
eli5.show_prediction(lr_model.named_steps["model"],
                     X_test.iloc[[i]],
                     feature_names=feature_names, show_feature_values=True, top=20)

#### SVM

In [29]:
eli5.show_prediction(svm_model.named_steps["model"],
                     X_test.iloc[[i]],
                     feature_names=feature_names, show_feature_values=True, top=20)

# What is "BIAS"?

```
Here the explanation for a single prediction is calculated by following the decision path in the tree, and adding up contribution of each feature from each node crossed into the overall probability predicted. So bascially, it's everything combined.
```

## Running on KIRC and KIRP